![Logo 1](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech1.jpg)
<div class="alert alert-block alert-info">
<h1> Modelowanie Języka</h1>
<h2> 10. <i>Model rekurencyjny z atencją</i>  [ćwiczenia]</h2> 
<h3> Jakub Pokrywka (2022)</h3>
</div>

![Logo 2](https://git.wmi.amu.edu.pl/AITech/Szablon/raw/branch/master/Logotyp_AITech2.jpg)

notebook na podstawie:

# https://pytorch.org/tutorials/intermediate/seq2seq_translation_tutorial.html

In [2]:
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import string
import re
import random

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

In [3]:
SOS_token = 0
EOS_token = 1

class Lang:
    def __init__(self):
        self.word2index = {}
        self.word2count = {}
        self.index2word = {0: "SOS", 1: "EOS"}
        self.n_words = 2  # Count SOS and EOS

    def addSentence(self, sentence):
        for word in sentence.split(' '):
            self.addWord(word)

    def addWord(self, word):
        if word not in self.word2index:
            self.word2index[word] = self.n_words
            self.word2count[word] = 1
            self.index2word[self.n_words] = word
            self.n_words += 1
        else:
            self.word2count[word] += 1

In [4]:
# def unicodeToAscii(s):
#     return ''.join(
#         c for c in unicodedata.normalize('NFD', s)
#         if unicodedata.category(c) != 'Mn'
#     )

In [5]:
pairs = []
with open('data/eng-pol.txt') as f:
    for line in f:
        eng_line, pol_line = line.lower().rstrip().split('\t')

        eng_line = re.sub(r"([.!?])", r" \1", eng_line)
        eng_line = re.sub(r"[^a-zA-Z.!?]+", r" ", eng_line)

        pol_line = re.sub(r"([.!?])", r" \1", pol_line)
        pol_line = re.sub(r"[^a-zA-Z.!?ąćęłńóśźżĄĆĘŁŃÓŚŹŻ]+", r" ", pol_line)
        
#         eng_line = unicodeToAscii(eng_line)
#         pol_line = unicodeToAscii(pol_line)

        pairs.append([eng_line, pol_line])




In [6]:
pairs[1]

['hi .', 'cześć .']

In [7]:
MAX_LENGTH = 10
eng_prefixes = (
    "i am ", "i m ",
    "he is", "he s ",
    "she is", "she s ",
    "you are", "you re ",
    "we are", "we re ",
    "they are", "they re "
)

pairs = [p for p in pairs if len(p[0].split(' ')) < MAX_LENGTH and len(p[1].split(' ')) < MAX_LENGTH]
pairs = [p for p in pairs if p[0].startswith(eng_prefixes)]

eng_lang = Lang()
pol_lang = Lang()

for pair in pairs:
    eng_lang.addSentence(pair[0])
    pol_lang.addSentence(pair[1])

In [8]:
pairs[0]

['i m ok .', 'ze mną wszystko w porządku .']

In [9]:
pairs[1]

['i m up .', 'wstałem .']

In [10]:
pairs[2]

['i m tom .', 'jestem tom .']

In [11]:
class EncoderRNN(nn.Module):
    def __init__(self, input_size, hidden_size):
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(input_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)

    def forward(self, input, hidden):
        embedded = self.embedding(input).view(1, 1, -1)
        output = embedded
        output, hidden = self.gru(output, hidden)
        return output, hidden

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

In [12]:
class DecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size):
        super(DecoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(output_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size)
        self.out = nn.Linear(hidden_size, output_size)
        self.softmax = nn.LogSoftmax(dim=1)

    def forward(self, input, hidden):
        output = self.embedding(input).view(1, 1, -1)
        output = F.relu(output)
        output, hidden = self.gru(output, hidden)
        output = self.softmax(self.out(output[0]))
        return output, hidden

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

In [13]:
class AttnDecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size, dropout_p=0.1, max_length=MAX_LENGTH):
        super(AttnDecoderRNN, self).__init__()
        self.hidden_size = hidden_size
        self.output_size = output_size
        self.dropout_p = dropout_p
        self.max_length = max_length

        self.embedding = nn.Embedding(self.output_size, self.hidden_size)
        self.attn = nn.Linear(self.hidden_size * 2, self.max_length)
        self.attn_combine = nn.Linear(self.hidden_size * 2, self.hidden_size)
        self.dropout = nn.Dropout(self.dropout_p)
        self.gru = nn.GRU(self.hidden_size, self.hidden_size)
        self.out = nn.Linear(self.hidden_size, self.output_size)

    def forward(self, input, hidden, encoder_outputs):
        embedded = self.embedding(input).view(1, 1, -1)
        embedded = self.dropout(embedded)

        attn_weights = F.softmax(
            self.attn(torch.cat((embedded[0], hidden[0]), 1)), dim=1)
        attn_applied = torch.bmm(attn_weights.unsqueeze(0),
                                 encoder_outputs.unsqueeze(0))

        output = torch.cat((embedded[0], attn_applied[0]), 1)
        output = self.attn_combine(output).unsqueeze(0)

        output = F.relu(output)
        output, hidden = self.gru(output, hidden)

        output = F.log_softmax(self.out(output[0]), dim=1)
        return output, hidden, attn_weights

    def initHidden(self):
        return torch.zeros(1, 1, self.hidden_size, device=device)

In [14]:
def tensorFromSentence(sentence, lang):
    indexes = [lang.word2index[word] for word in sentence.split(' ')]
    indexes.append(EOS_token)
    return torch.tensor(indexes, dtype=torch.long, device=device).view(-1, 1)


In [15]:
teacher_forcing_ratio = 0.5

def train_one_batch(input_tensor, target_tensor, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion, max_length=MAX_LENGTH):
    encoder_hidden = encoder.initHidden()

    encoder_optimizer.zero_grad()
    decoder_optimizer.zero_grad()

    input_length = input_tensor.size(0)
    target_length = target_tensor.size(0)

    encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

    loss = 0

    for ei in range(input_length):
        encoder_output, encoder_hidden = encoder(input_tensor[ei], encoder_hidden)
        encoder_outputs[ei] = encoder_output[0, 0]

    decoder_input = torch.tensor([[SOS_token]], device=device)

    decoder_hidden = encoder_hidden

    use_teacher_forcing = True if random.random() < teacher_forcing_ratio else False

    if use_teacher_forcing:
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(decoder_input, decoder_hidden, encoder_outputs)
            loss += criterion(decoder_output, target_tensor[di])
            decoder_input = target_tensor[di]  # Teacher forcing

    else:
        for di in range(target_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(decoder_input, decoder_hidden, encoder_outputs)
            topv, topi = decoder_output.topk(1)
            decoder_input = topi.squeeze().detach()  # detach from history as input

            loss += criterion(decoder_output, target_tensor[di])
            if decoder_input.item() == EOS_token:
                break

    loss.backward()

    encoder_optimizer.step()
    decoder_optimizer.step()

    return loss.item() / target_length

In [16]:
def trainIters(encoder, decoder, n_iters, print_every=1000, learning_rate=0.01):
    print_loss_total = 0  # Reset every print_every

    encoder_optimizer = optim.SGD(encoder.parameters(), lr=learning_rate)
    decoder_optimizer = optim.SGD(decoder.parameters(), lr=learning_rate)
    
    training_pairs = [random.choice(pairs) for _ in range(n_iters)]
    training_pairs = [(tensorFromSentence(p[0], eng_lang), tensorFromSentence(p[1], pol_lang)) for p in training_pairs]
    
    criterion = nn.NLLLoss()

    for i in range(1, n_iters + 1):
        training_pair = training_pairs[i - 1]
        input_tensor = training_pair[0]
        target_tensor = training_pair[1]

        loss = train_one_batch(input_tensor,
                               target_tensor,
                               encoder,
                               decoder,
                               encoder_optimizer,
                               decoder_optimizer,
                               criterion)
        
        print_loss_total += loss

        if i % print_every == 0:
            print_loss_avg = print_loss_total / print_every
            print_loss_total = 0
            print(f'iter: {i}, loss: {print_loss_avg}')


In [17]:
def evaluate(encoder, decoder, sentence, max_length=MAX_LENGTH):
    with torch.no_grad():
        input_tensor = tensorFromSentence(sentence, eng_lang)
        input_length = input_tensor.size()[0]
        encoder_hidden = encoder.initHidden()

        encoder_outputs = torch.zeros(max_length, encoder.hidden_size, device=device)

        for ei in range(input_length):
            encoder_output, encoder_hidden = encoder(input_tensor[ei],
                                                     encoder_hidden)
            encoder_outputs[ei] += encoder_output[0, 0]

        decoder_input = torch.tensor([[SOS_token]], device=device)  # SOS

        decoder_hidden = encoder_hidden

        decoded_words = []
        decoder_attentions = torch.zeros(max_length, max_length)

        for di in range(max_length):
            decoder_output, decoder_hidden, decoder_attention = decoder(
                decoder_input, decoder_hidden, encoder_outputs)
            decoder_attentions[di] = decoder_attention.data
            topv, topi = decoder_output.data.topk(1)
            if topi.item() == EOS_token:
                decoded_words.append('<EOS>')
                break
            else:
                decoded_words.append(pol_lang.index2word[topi.item()])

            decoder_input = topi.squeeze().detach()

        return decoded_words, decoder_attentions[:di + 1]

In [18]:
def evaluateRandomly(encoder, decoder, n=10):
    for i in range(n):
        pair = random.choice(pairs)
        print('>', pair[0])
        print('=', pair[1])
        output_words, attentions = evaluate(encoder, decoder, pair[0])
        output_sentence = ' '.join(output_words)
        print('<', output_sentence)
        print('')

In [19]:
hidden_size = 256
encoder1 = EncoderRNN(eng_lang.n_words, hidden_size).to(device)
attn_decoder1 = AttnDecoderRNN(hidden_size, pol_lang.n_words, dropout_p=0.1).to(device)

trainIters(encoder1, attn_decoder1, 75000, print_every=50)

iter: 50, loss: 5.242557571774437
iter: 100, loss: 4.278488328888303
iter: 150, loss: 4.345584976514179
iter: 200, loss: 4.372515664100646
iter: 250, loss: 4.305285846165248
iter: 300, loss: 4.340697079749336
iter: 350, loss: 4.225462563787189
iter: 400, loss: 3.931193191331531
iter: 450, loss: 4.255609704971314
iter: 500, loss: 4.110652269242301
iter: 550, loss: 4.10534066640763
iter: 600, loss: 4.21553361088889
iter: 650, loss: 4.182825716926937
iter: 700, loss: 4.125172647006929
iter: 750, loss: 3.92194454044766
iter: 800, loss: 3.9588410959697904
iter: 850, loss: 4.045722855431693
iter: 900, loss: 3.989374102009668
iter: 950, loss: 3.8188858143791307
iter: 1000, loss: 4.083652021286979
iter: 1050, loss: 3.853677998118931
iter: 1100, loss: 4.240768341064452
iter: 1150, loss: 3.9389620546991857
iter: 1200, loss: 3.797674254826137
iter: 1250, loss: 3.9533765572441957
iter: 1300, loss: 4.227734768761528
iter: 1350, loss: 4.098812954554482
iter: 1400, loss: 3.970981749352953
iter: 1450,

iter: 11300, loss: 2.534775358722323
iter: 11350, loss: 2.3763021782466343
iter: 11400, loss: 2.477060817866099
iter: 11450, loss: 2.240788399741763
iter: 11500, loss: 2.4560615454931103
iter: 11550, loss: 2.4167706055300577
iter: 11600, loss: 2.5485691031482482
iter: 11650, loss: 2.4385872491881964
iter: 11700, loss: 2.262665515203325
iter: 11750, loss: 2.3140043601195015
iter: 11800, loss: 2.3840308377969834
iter: 11850, loss: 2.3109344417519044
iter: 11900, loss: 2.3575586484140825
iter: 11950, loss: 2.2054063754535855
iter: 12000, loss: 2.256502300773348
iter: 12050, loss: 2.4794748330608245
iter: 12100, loss: 2.337028050218309
iter: 12150, loss: 2.0973778800964356
iter: 12200, loss: 2.159631293109485
iter: 12250, loss: 2.3099975161770034
iter: 12300, loss: 2.421918697101729
iter: 12350, loss: 2.531752646151043
iter: 12400, loss: 2.320960243735995
iter: 12450, loss: 2.2293582723708387
iter: 12500, loss: 2.2750969548414623
iter: 12550, loss: 1.7618893385950534
iter: 12600, loss: 2.3

iter: 22200, loss: 1.6116164426425141
iter: 22250, loss: 1.2793350757350999
iter: 22300, loss: 1.3017940769725374
iter: 22350, loss: 1.3736145087998537
iter: 22400, loss: 1.138627294466609
iter: 22450, loss: 1.310434480055457
iter: 22500, loss: 1.3961503054835491
iter: 22550, loss: 1.3724343404996964
iter: 22600, loss: 1.3563060793403596
iter: 22650, loss: 1.5050592094120523
iter: 22700, loss: 1.3752844895202485
iter: 22750, loss: 1.1653902740024384
iter: 22800, loss: 1.586769177135967
iter: 22850, loss: 1.2032956434232844
iter: 22900, loss: 1.3740250343538463
iter: 22950, loss: 1.1050300681430192
iter: 23000, loss: 1.2519222570203599
iter: 23050, loss: 1.42347088217688
iter: 23100, loss: 1.4116886373684991
iter: 23150, loss: 1.1194891034222785
iter: 23200, loss: 1.2006812089085581
iter: 23250, loss: 1.4476829275015806
iter: 23300, loss: 1.3017136716679447
iter: 23350, loss: 1.3050824448059475
iter: 23400, loss: 1.0946670590383667
iter: 23450, loss: 1.0267400648877734
iter: 23500, loss

KeyboardInterrupt: 

In [20]:
evaluateRandomly(encoder1, attn_decoder1)

> he s a very important person .
= on jest bardzo ważnym człowiekiem .
< on jest bardzo ważnym człowiekiem . <EOS>

> i m beautiful .
= jestem piękny .
< jestem piękna . <EOS>

> we re quite certain of that .
= jesteśmy tego całkiem pewni .
< jesteśmy tego całkiem pewni . <EOS>

> we are all looking forward to seeing you .
= miło nam będzie ponownie się z panem spotkać .
< miło nam nam ponownie się z tobą . . <EOS>

> i m inside .
= jestem w środku .
< jestem w środku . <EOS>

> i m giving up smoking .
= rzucam palenie .
< rzuciłem palenie . <EOS>

> we re not arguing .
= nie kłócimy się .
< nie wychodzimy . <EOS>

> i m not prepared to do that yet .
= nie jestem jeszcze przygotowany żeby to zrobić .
< nie jestem jeszcze przygotowany żeby to zrobić . <EOS>

> i m a free man .
= jestem wolnym człowiekiem .
< jestem wolnym człowiekiem . <EOS>

> i m still on the clock .
= jeszcze jestem w pracy .
< wciąż jestem w domu . <EOS>



In [21]:
pairs[0]

['i m ok .', 'ze mną wszystko w porządku .']